In [3]:
import os
os.chdir('..')
print(os.getcwd())

/mnt/SamsungSSD/workspace/yoshioka/rendering


In [4]:
import plotly.graph_objects as go


def add_mesh(fig, mesh):
    # fig = go.Figure()
    x, y, z = mesh.vertices.T
    i, j, k = mesh.faces.T
    fig.add_trace(
        go.Mesh3d(x=x,y=y,z=z,i=i,j=j,k=k)
    )
    return fig

In [48]:
from utils.mano import ManoLayer
from utils.utils import load_ho_meta, get_obj_mesh, apply_transform_to_mesh
import trimesh


mano = ManoLayer()
anno = load_ho_meta("data/HO3D_v3/train/ABF10/meta/0100.pkl")

mano_verts = mano(anno)

obj_verts, obj_faces, obj_uv, obj_map = get_obj_mesh(anno)
obj_verts = apply_transform_to_mesh(obj_verts, anno)


print(mano_verts.shape, mano.faces.shape)
mano_mesh = trimesh.Trimesh(vertices=mano_verts[0], faces=mano.faces, )
obj_mesh = trimesh.Trimesh(vertices=obj_verts, faces=obj_faces)
# scene = trimesh.Scene([mano_mesh, obj_mesh])
# lights, transforms = trimesh.scene.lighting.autolight(scene)

# scene.show()

/mnt/SamsungSSD/workspace/yoshioka/rendering/utils/utils.py:15: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



torch.Size([8251, 3]) torch.Size([3, 3]) torch.Size([3])
torch.Size([1, 778, 3]) torch.Size([1538, 3])


In [49]:
fig = go.Figure()
fig = add_mesh(fig, mano_mesh)
fig = add_mesh(fig, obj_mesh)
fig.show()

In [50]:
# import plotly.figure_factory as ff
import numpy as np

proximity_inds = np.array(
    "228 168  10  74  75 288 379 142 266  64  64   9  62 150 151 132  74  77 \
    74 776 770 275 271 275  63 775 774 152  93  63  69  63 148 147  67 157\
    268  66 775  72  73  73 268  69 148  70 285 607 582 625 682 604 489 496\
    496 470 469 507 565 550 564 141 379 386 358 358 357 397 454 439 453 171\
    194  48  47 238 341 342 329 342 171 704 700 714 760 756 761 763 764 768\
    744 735 745 759 763 683 695 159 157 157  99  27  25  24".split()).astype(int)
proximity_inds

proximity_verts = mano_verts[0][proximity_inds]

import torch

def calc_face_normals(verts, faces):
    v1 = verts[faces[:,0].type(torch.long)]
    v2 = verts[faces[:,1].type(torch.long)]
    v3 = verts[faces[:,2].type(torch.long)]
    return np.cross(v2-v1, v3-v1)

def calc_vertex_normals(verts, faces):
    face_normals = calc_face_normals(verts, faces)
    vertex_normals = np.zeros(verts.shape)
    for i, face in enumerate(faces):
        vertex_normals[face] += face_normals[i]
    vertex_normals = vertex_normals / np.linalg.norm(vertex_normals, axis=1)[:,None]
    return vertex_normals

proximity_normals = calc_vertex_normals(mano_verts[0], mano.faces)[proximity_inds]
print(np.linalg.norm(proximity_normals, axis=1))

fig = go.Figure()
fig = add_mesh(fig, mano_mesh)
fig = add_mesh(fig, obj_mesh)
fig.add_trace(
    # go.Scatter3d(
    #     x=proximity_verts[:,0], 
    #     y=proximity_verts[:,1], 
    #     z=proximity_verts[:,2], 
    #     mode='markers', marker=dict(size=1))
    go.Cone(
        x=proximity_verts[:,0], 
        y=proximity_verts[:,1], 
        z=proximity_verts[:,2], 
        u=proximity_normals[:,0],
        v=proximity_normals[:,1],
        w=proximity_normals[:,2],
        colorscale='Greens',
        # sizemode="absolute",
        sizeref=5,
    )
)
fig.show()

[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1.]


In [51]:
import trimesh

ray_origins = proximity_verts.numpy()
ray_directions = proximity_normals

locations, index_ray, index_tri = obj_mesh.ray.intersects_location(
    ray_origins=ray_origins, 
    ray_directions=ray_directions
)
print(index_ray)
# print(locations)

ray_distances = np.linalg.norm(locations - ray_origins[index_ray], axis=1)
print(ray_distances)

[84 80 71 16  3 18 58 14 49 89 10  9 96 66 88 73  1 10  9 54 53 93  2 79
 77  0 14 24 31 29 24 31 29 72 68 15  0 72 75 13 13 60  6 62 55 54 53 27
 59 76 75 74 63 80 71  4 22 69 78 17  1  5 79 77 15  5 17 86 86 69 16  3
 18 87 94 22 68 84 66 67  4 93 56 49 60 74 61 12 70 63 65 64 88  7 87 94
 27 56 12 55 95 78 58 73 89 57 96  7 59 61 57 76  2 70 65 64 67 95  6 62]
[0.08296057 0.01330541 0.01330541 0.03626676 0.03626676 0.03626676
 0.0579711  0.08491488 0.03889077 0.03719085 0.02322982 0.02322982
 0.08858801 0.01379583 0.10874972 0.0060197  0.05572434 0.05445522
 0.05445522 0.02616022 0.02616022 0.05537446 0.03784318 0.00589136
 0.00589136 0.10948637 0.02743266 0.04920934 0.04920934 0.04920934
 0.03765163 0.03765163 0.03765163 0.00346596 0.00880317 0.06343369
 0.02146002 0.06064994 0.00643662 0.02309446 0.11407166 0.05688026
 0.041742   0.041742   0.01984953 0.05273246 0.05273246 0.03767148
 0.0042645  0.06050254 0.06001945 0.05574014 0.01273383 0.05303968
 0.05303968 0.10589568 0.032578

In [56]:
proximity_d = proximity_normals.copy()
proximity_d[index_ray] *= ray_distances[:, None] 
index_out = np.setdiff1d(np.arange(len(proximity_verts)), index_ray)
proximity_d[index_out] *= 10


fig = go.Figure()
fig = add_mesh(fig, mano_mesh)
fig = add_mesh(fig, obj_mesh)
fig.add_trace(
    # go.Scatter3d(
    #     x=proximity_verts[:,0], 
    #     y=proximity_verts[:,1], 
    #     z=proximity_verts[:,2], 
    #     mode='markers', marker=dict(size=1))
    # go.Cone(
    #     x=proximity_verts[:,0], 
    #     y=proximity_verts[:,1], 
    #     z=proximity_verts[:,2], 
    #     u=proximity_d[:,0],
    #     v=proximity_d[:,1],
    #     w=proximity_d[:,2],
    #     # colorscale='Greens',
    #     sizemode="scaled",
    #     sizeref=10,
    # )
    go.Cone(
        x=proximity_verts[index_ray,0], 
        y=proximity_verts[index_ray,1], 
        z=proximity_verts[index_ray,2], 
        u=proximity_d[index_ray,0],
        v=proximity_d[index_ray,1],
        w=proximity_d[index_ray,2],
        # colorscale='Greens',
        sizemode="scaled",
        sizeref=10,
    )
)
# fig.add_trace(
#     go.Cone(
#         x=proximity_verts[index_out,0], 
#         y=proximity_verts[index_out,1], 
#         z=proximity_verts[index_out,2], 
#         u=proximity_d[index_out,0],
#         v=proximity_d[index_out,1],
#         w=proximity_d[index_out,2],
#         colorscale='Greens',
#         sizemode="scaled",
#         sizeref=10,
#     ))
fig.show()